## Data cleaning and indexing in ElasticSearch

In [9]:
import os
import re
import time
import sys
import copy
import email as e
import random 
import numpy as np
import pandas as pd
from sklearn import linear_model
from sklearn.metrics import accuracy_score
from bs4 import BeautifulSoup
from elasticsearch import Elasticsearch 
import math
import string

In [10]:
email_dic = {}
def indexfile(dataSet, labelDict, setname):
    for file in dataSet:
        print('Processing file ' + file)
        with open(file, 'r',encoding="utf8",errors = "ignore") as f:
            fileData = f.read()
            data = fileData.replace('\n', ' ').replace('\t', '')

            words = data.split()
            withoutStopwords= list()

            for i in range(len(words)):
                if re.match("^[A-Za-z]*$", words[i]):
                    if words[i] in stopwords:
                        withoutStopwords.append('')
                    else:
                        withoutStopwords.append(words[i])
                else:
                    withoutStopwords.append('')
            text = ' '.join(withoutStopwords)
            text = re.sub(' +', ' ', text)
            text = text.lower()

            for p in string.punctuation:
                if p != '_' and p != '-' and p != '\'':
                    text = text.replace(p, " ")
            text = text.replace("  ", " ")
            text = BeautifulSoup(text, "html.parser").text

            dataFile = f.name.split('/')[2]
            print(dataFile)

            if labelDict[dataFile] == '1':
                spamVal = 'spam'
            else:
                spamVal = 'ham'

            bodyText = {
                'file_name': dataFile,
                'label': spamVal,
                'body': text,
                'split': setname
            }

            es.index(index='spam_test2', doc_type='document', id=dataFile, body=bodyText)

            email_dic[file] = bodyText

es = Elasticsearch()
stopwords = list()
dictionary = list()
es.indices.delete(index="spam_test2", ignore=[400, 404])
with open('stoplist.txt', 'r') as f:
    for line in f.readlines():
        word = line.replace('\n', '')
        stopwords.append(word)

label_path = 'trec07p/full'

for dir_path, dir_names, file_names in os.walk('trec07p/data'):
    allfiles = [os.path.join(dir_path, filename).replace("\\", "/") for filename in file_names]
training = allfiles
test = list(random.sample(training, int(math.floor(.2 * len(training)))))
for i in test:
    training.remove(i)

labelDict = dict()
with open('trec07p/full/index', 'r') as f:
    for line in f:
            label_list = line.split()
            labelDict[label_list[1].split('/')[2]] = '1' if label_list[0] == 'spam' else '0'

es.indices.create(index="spam_test2",
                      body={
                          'settings': {
                              'index': {
                                  'store': {
                                      'type': "default"
                                  },
                                  'number_of_shards': 1,
                                  'number_of_replicas': 1
                              },
                              'analysis': {
                                  'analyzer': {
                                      'my_english': {
                                          'type': 'english',
                                          'stopwords_path': 'stoplist.txt'
                                      }
                                  }
                              }
                          },
                          "mappings": {
                              "document": {
                                  "properties": {
                                      "file_name": {
                                          "type": "text",
                                          "store": True,
                                          "index": "not_analyzed"
                                      },
                                      "body": {
                                          "type": "text",
                                          "store": True,
                                          "index": "analyzed",
                                          "term_vector": "with_positions_offsets_payloads",
                                          "analyzer": "my_english"
                                      },
                                      "label":{
                                          "type": "text",
                                          "store": True,
                                          "index": "not_analyzed"
                                      },
                                      "split": {
                                          "type": "text",
                                          "store": True,
                                          "index": "not_analyzed"
                                      }
                                  }
                              }
                          }
                      })

indexfile(allfiles, labelDict, 'all')


Processing file trec07p/data/inmail.10
inmail.10
Processing file trec07p/data/inmail.100
inmail.100
Processing file trec07p/data/inmail.1000
inmail.1000
Processing file trec07p/data/inmail.10000
inmail.10000
Processing file trec07p/data/inmail.10001
inmail.10001
Processing file trec07p/data/inmail.10002
inmail.10002
Processing file trec07p/data/inmail.10003
inmail.10003
Processing file trec07p/data/inmail.10004
inmail.10004
Processing file trec07p/data/inmail.10006
inmail.10006
Processing file trec07p/data/inmail.10007
inmail.10007
Processing file trec07p/data/inmail.10008
inmail.10008
Processing file trec07p/data/inmail.10009
inmail.10009
Processing file trec07p/data/inmail.1001
inmail.1001
Processing file trec07p/data/inmail.10010
inmail.10010
Processing file trec07p/data/inmail.10011
inmail.10011
Processing file trec07p/data/inmail.10012
inmail.10012
Processing file trec07p/data/inmail.10013
inmail.10013
Processing file trec07p/data/inmail.10015
inmail.10015
Processing file trec07p/

Processing file trec07p/data/inmail.1016
inmail.1016
Processing file trec07p/data/inmail.10161
inmail.10161
Processing file trec07p/data/inmail.10163
inmail.10163
Processing file trec07p/data/inmail.10164
inmail.10164
Processing file trec07p/data/inmail.10165
inmail.10165
Processing file trec07p/data/inmail.10166
inmail.10166
Processing file trec07p/data/inmail.10167
inmail.10167
Processing file trec07p/data/inmail.10170
inmail.10170
Processing file trec07p/data/inmail.10171
inmail.10171
Processing file trec07p/data/inmail.10172
inmail.10172
Processing file trec07p/data/inmail.10173
inmail.10173
Processing file trec07p/data/inmail.10174
inmail.10174
Processing file trec07p/data/inmail.10175
inmail.10175
Processing file trec07p/data/inmail.10176
inmail.10176
Processing file trec07p/data/inmail.10177
inmail.10177
Processing file trec07p/data/inmail.10178
inmail.10178
Processing file trec07p/data/inmail.10179
inmail.10179
Processing file trec07p/data/inmail.1018
inmail.1018
Processing fil

inmail.10328
Processing file trec07p/data/inmail.1033
inmail.1033
Processing file trec07p/data/inmail.10330
inmail.10330
Processing file trec07p/data/inmail.10331
inmail.10331
Processing file trec07p/data/inmail.10332
inmail.10332
Processing file trec07p/data/inmail.10333
inmail.10333
Processing file trec07p/data/inmail.10334
inmail.10334
Processing file trec07p/data/inmail.10338
inmail.10338
Processing file trec07p/data/inmail.10339
inmail.10339
Processing file trec07p/data/inmail.1034
inmail.1034
Processing file trec07p/data/inmail.10341
inmail.10341
Processing file trec07p/data/inmail.10343
inmail.10343
Processing file trec07p/data/inmail.10344
inmail.10344
Processing file trec07p/data/inmail.10345
inmail.10345
Processing file trec07p/data/inmail.10346
inmail.10346
Processing file trec07p/data/inmail.10347
inmail.10347
Processing file trec07p/data/inmail.10348
inmail.10348
Processing file trec07p/data/inmail.10349
inmail.10349
Processing file trec07p/data/inmail.1035
inmail.1035
Pro

inmail.10500
Processing file trec07p/data/inmail.10501
inmail.10501
Processing file trec07p/data/inmail.10502
inmail.10502
Processing file trec07p/data/inmail.10503
inmail.10503
Processing file trec07p/data/inmail.10504
inmail.10504
Processing file trec07p/data/inmail.10505
inmail.10505
Processing file trec07p/data/inmail.10506
inmail.10506
Processing file trec07p/data/inmail.10507
inmail.10507
Processing file trec07p/data/inmail.10508
inmail.10508
Processing file trec07p/data/inmail.10509
inmail.10509
Processing file trec07p/data/inmail.1051
inmail.1051
Processing file trec07p/data/inmail.10510
inmail.10510
Processing file trec07p/data/inmail.10511
inmail.10511
Processing file trec07p/data/inmail.10512
inmail.10512
Processing file trec07p/data/inmail.10513
inmail.10513
Processing file trec07p/data/inmail.10514
inmail.10514
Processing file trec07p/data/inmail.10516
inmail.10516
Processing file trec07p/data/inmail.10517
inmail.10517
Processing file trec07p/data/inmail.10518
inmail.10518

inmail.10661
Processing file trec07p/data/inmail.10662
inmail.10662
Processing file trec07p/data/inmail.10663
inmail.10663
Processing file trec07p/data/inmail.10664
inmail.10664
Processing file trec07p/data/inmail.10665
inmail.10665
Processing file trec07p/data/inmail.10666
inmail.10666
Processing file trec07p/data/inmail.10667
inmail.10667
Processing file trec07p/data/inmail.10668
inmail.10668
Processing file trec07p/data/inmail.1067
inmail.1067
Processing file trec07p/data/inmail.10671
inmail.10671
Processing file trec07p/data/inmail.10672
inmail.10672
Processing file trec07p/data/inmail.10674
inmail.10674
Processing file trec07p/data/inmail.10675
inmail.10675
Processing file trec07p/data/inmail.10676
inmail.10676
Processing file trec07p/data/inmail.10677
inmail.10677
Processing file trec07p/data/inmail.10679
inmail.10679
Processing file trec07p/data/inmail.1068
inmail.1068
Processing file trec07p/data/inmail.10680
inmail.10680
Processing file trec07p/data/inmail.10681
inmail.10681
P

...

Processing file trec07p/data/inmail.9222
inmail.9222
Processing file trec07p/data/inmail.9223
inmail.9223
Processing file trec07p/data/inmail.9224
inmail.9224
Processing file trec07p/data/inmail.9228
inmail.9228
Processing file trec07p/data/inmail.923
inmail.923
Processing file trec07p/data/inmail.9230
inmail.9230
Processing file trec07p/data/inmail.9231
inmail.9231
Processing file trec07p/data/inmail.9232
inmail.9232
Processing file trec07p/data/inmail.9234
inmail.9234
Processing file trec07p/data/inmail.9235
inmail.9235
Processing file trec07p/data/inmail.9236
inmail.9236
Processing file trec07p/data/inmail.9237
inmail.9237
Processing file trec07p/data/inmail.9238
inmail.9238
Processing file trec07p/data/inmail.9239
inmail.9239
Processing file trec07p/data/inmail.924
inmail.924
Processing file trec07p/data/inmail.9240
inmail.9240
Processing file trec07p/data/inmail.9241
inmail.9241
Processing file trec07p/data/inmail.9242
inmail.9242
Processing file trec07p/data/inmail.9245
inmail.92

inmail.9401
Processing file trec07p/data/inmail.9402
inmail.9402
Processing file trec07p/data/inmail.9403
inmail.9403
Processing file trec07p/data/inmail.9404
inmail.9404
Processing file trec07p/data/inmail.9405
inmail.9405
Processing file trec07p/data/inmail.9406
inmail.9406
Processing file trec07p/data/inmail.9408
inmail.9408
Processing file trec07p/data/inmail.9409
inmail.9409
Processing file trec07p/data/inmail.941
inmail.941
Processing file trec07p/data/inmail.9410
inmail.9410
Processing file trec07p/data/inmail.9411
inmail.9411
Processing file trec07p/data/inmail.9412
inmail.9412
Processing file trec07p/data/inmail.9413
inmail.9413
Processing file trec07p/data/inmail.9414
inmail.9414
Processing file trec07p/data/inmail.9415
inmail.9415
Processing file trec07p/data/inmail.9417
inmail.9417
Processing file trec07p/data/inmail.9419
inmail.9419
Processing file trec07p/data/inmail.942
inmail.942
Processing file trec07p/data/inmail.9420
inmail.9420
Processing file trec07p/data/inmail.94

Processing file trec07p/data/inmail.9584
inmail.9584
Processing file trec07p/data/inmail.9585
inmail.9585
Processing file trec07p/data/inmail.9586
inmail.9586
Processing file trec07p/data/inmail.9587
inmail.9587
Processing file trec07p/data/inmail.9588
inmail.9588
Processing file trec07p/data/inmail.9589
inmail.9589
Processing file trec07p/data/inmail.9590
inmail.9590
Processing file trec07p/data/inmail.9591
inmail.9591
Processing file trec07p/data/inmail.9592
inmail.9592
Processing file trec07p/data/inmail.9594
inmail.9594
Processing file trec07p/data/inmail.9595
inmail.9595
Processing file trec07p/data/inmail.9596
inmail.9596
Processing file trec07p/data/inmail.9597
inmail.9597
Processing file trec07p/data/inmail.9598
inmail.9598
Processing file trec07p/data/inmail.960
inmail.960
Processing file trec07p/data/inmail.9600
inmail.9600
Processing file trec07p/data/inmail.9601
inmail.9601
Processing file trec07p/data/inmail.9602
inmail.9602
Processing file trec07p/data/inmail.9603
inmail.

Processing file trec07p/data/inmail.9748
inmail.9748
Processing file trec07p/data/inmail.975
inmail.975
Processing file trec07p/data/inmail.9750
inmail.9750
Processing file trec07p/data/inmail.9751
inmail.9751
Processing file trec07p/data/inmail.9752
inmail.9752
Processing file trec07p/data/inmail.9753
inmail.9753
Processing file trec07p/data/inmail.9754
inmail.9754
Processing file trec07p/data/inmail.9755
inmail.9755
Processing file trec07p/data/inmail.9756
inmail.9756
Processing file trec07p/data/inmail.9757
inmail.9757
Processing file trec07p/data/inmail.9758
inmail.9758
Processing file trec07p/data/inmail.9759
inmail.9759
Processing file trec07p/data/inmail.9760
inmail.9760
Processing file trec07p/data/inmail.9761
inmail.9761
Processing file trec07p/data/inmail.9762
inmail.9762
Processing file trec07p/data/inmail.9763
inmail.9763
Processing file trec07p/data/inmail.9764
inmail.9764
Processing file trec07p/data/inmail.9765
inmail.9765
Processing file trec07p/data/inmail.9766
inmail.

inmail.9919
Processing file trec07p/data/inmail.992
inmail.992
Processing file trec07p/data/inmail.9920
inmail.9920
Processing file trec07p/data/inmail.9921
inmail.9921
Processing file trec07p/data/inmail.9922
inmail.9922
Processing file trec07p/data/inmail.9923
inmail.9923
Processing file trec07p/data/inmail.9925
inmail.9925
Processing file trec07p/data/inmail.9926
inmail.9926
Processing file trec07p/data/inmail.9927
inmail.9927
Processing file trec07p/data/inmail.9928
inmail.9928
Processing file trec07p/data/inmail.9929
inmail.9929
Processing file trec07p/data/inmail.9932
inmail.9932
Processing file trec07p/data/inmail.9934
inmail.9934
Processing file trec07p/data/inmail.9937
inmail.9937
Processing file trec07p/data/inmail.9938
inmail.9938
Processing file trec07p/data/inmail.9939
inmail.9939
Processing file trec07p/data/inmail.994
inmail.994
Processing file trec07p/data/inmail.9940
inmail.9940
Processing file trec07p/data/inmail.9941
inmail.9941
Processing file trec07p/data/inmail.99

In [11]:
email_content_dict = email_dic

In [12]:
def put_data_in_ES(email_content_dict):
    i = 1
    docid_to_es_id_mapping = {}
    for key in email_content_dict:
        es_doc = {"doc_id" : key, "content":email_content_dict[key]}
#         es.index(index = "classifier", doc_type = "emails", id = i, body = es_doc)
        if i % 100 == 0:
            print ("At email: ", i)
        docid_to_es_id_mapping[key] = i
        i += 1
    return docid_to_es_id_mapping
docid_to_es_id_mapping = put_data_in_ES(email_content_dict)

At email:  100
At email:  200
At email:  300
At email:  400
At email:  500
At email:  600
At email:  700
At email:  800
At email:  900
At email:  1000
At email:  1100
At email:  1200
At email:  1300
At email:  1400
At email:  1500
At email:  1600
At email:  1700
At email:  1800
At email:  1900
At email:  2000
At email:  2100
At email:  2200
At email:  2300
At email:  2400
At email:  2500
At email:  2600
At email:  2700
At email:  2800
At email:  2900
At email:  3000
At email:  3100
At email:  3200
At email:  3300
At email:  3400
At email:  3500
At email:  3600
At email:  3700
At email:  3800
At email:  3900
At email:  4000
At email:  4100
At email:  4200
At email:  4300
At email:  4400
At email:  4500
At email:  4600
At email:  4700
At email:  4800
At email:  4900
At email:  5000
At email:  5100
At email:  5200
At email:  5300
At email:  5400
At email:  5500
At email:  5600
At email:  5700
At email:  5800
At email:  5900
At email:  6000
At email:  6100
At email:  6200
At email:  6300
A

In [38]:
keyword_list = "free spam click buy clearance shopper order earn cash extra money double collect credit check affordable fast price loans profit refinance hidden freedom chance miracle lose home remove success virus malware ad subscribe sales performance viagra valium medicine diagnostics million join deal unsolicited trial prize now legal bonus limited instant luxury legal celebrity only compare win viagra discount click here meet singles incredible deal lose weight act now 100 percent dollar free fast cash million dollars lower interest rate visit our website no credit check"
column = list(set(keyword_list.split(" ")))
index = list(email_content_dict.keys())
index_list = [i.split("/")[-1] for i in index]
df = pd.DataFrame(0, columns = column, index = index_list)
# label
def label_collector():
    location = r"C:\Users\mm199\IR-hw\HW7_data\trec07p\full"
    list_of_email = os.listdir(location)
    filename = location + "\\" + "index"
    dict_label = {}
    with open(filename) as file:
        file = file.readlines()
        file = [i.strip("\n").split("/") for i in file]
        for element in file:
            label = element[0].split(" ")[0]
            if label.lower() == "spam":
                label = 1
            else:
                label = 0 
            dict_label[element[-1]] = label
    return dict_label
df_y_label = label_collector()       
        

In [59]:
len(index_list)

60336

In [52]:
for doc_id,doc_no in enumerate(index_list):
#     doc_id = docid_to_es_id_mapping[doc_no]
    dict_all = es.termvectors(index = "spam_test2", doc_type = "document", id = doc_no, term_statistics = True, fields = ["body"])
    for word in column:
        if dict_all["term_vectors"] != {}:
            temp_dict = dict_all["term_vectors"]["body"]["terms"]
        else:
            pass
        try:     
            tfwd = temp_dict[word]["term_freq"]
            if tfwd >= 1:
                tfwd = 1
        except:
            tfwd = 0
        df.set_value(doc_no, word, tfwd) 
    if doc_id % 1000 == 0 :
        print ("done",doc_id)


done 0
done 1000
done 2000
done 3000
done 4000
done 5000
done 6000
done 7000
done 8000
done 9000
done 10000
done 11000
done 12000
done 13000
done 14000
done 15000
done 16000
done 17000
done 18000
done 19000
done 20000
done 21000
done 22000
done 23000
done 24000
done 25000
done 26000
done 27000
done 28000
done 29000
done 30000
done 31000
done 32000
done 33000
done 34000
done 35000
done 36000
done 37000
done 38000
done 39000
done 40000
done 41000
done 42000
done 43000
done 44000
done 45000
done 46000
done 47000
done 48000
done 49000
done 50000
done 51000
done 52000
done 53000
done 54000
done 55000
done 56000
done 57000
done 58000
done 59000
done 60000


In [67]:
## randomly sample 80% of data for training
index_training = random.sample(index_list, k = int(len(index_list) * 0.80))
## make rest 20 % as testing
index_testing = (set(index_list) ^ set(index_training))
## get train and test dataframe
training_df = df.loc[index_training]
testing_df = df.loc[index_testing]
## get right label for randomly sampled train and test data
def get_actual_label(index_list):
    true_result = []
    for i in index_list:
        true_result.append(df_y_label[i])
    return true_result
training_result = get_actual_label(index_training)
testing_result = get_actual_label(index_testing)



72.539 %


In [ ]:
## Gaussian regression
from sklearn.naive_bayes import GaussianNB
nb_reg = GaussianNB()
fit_data = nb_reg.fit(training_df, training_result)
test_result = fit_data.predict(testing_df)
score = accuracy_score(y_true = testing_result, y_pred = test_result)
print (round((score * 100),3), "%")


In [72]:
from sklearn.svm import SVC

svc = SVC(kernel='sigmoid', gamma=1.0)
svc.fit(training_df, training_result)
prediction = svc.predict(testing_df)
accuracy_score(testing_result,test_result)

0.7253894597282068

In [54]:
df

clearance  million  trial  no  lose  price  shopper  click  \
inmail.1              0        0      0   0     0      0        0      0   
inmail.10             0        0      0   0     0      0        0      0   
inmail.100            0        0      0   0     0      0        0      0   
inmail.1000           0        0      0   0     0      0        0      1   
inmail.10000          0        1      0   0     0      0        0      0   
inmail.10001          0        0      0   0     0      0        0      0   
inmail.10002          0        0      0   0     0      0        0      0   
inmail.10003          0        0      0   0     0      0        0      0   
inmail.10004          0        0      0   0     0      0        0      0   
inmail.10005          0        0      0   0     0      1        0      0   
inmail.10007          0        0      0   0     0      0        0      0   
inmail.10008          0        0      0   0     0      0        0      0   
inmail.10009          0        0      0   0     0      0        0      0   
inmail.1001           0        0      0   0     0      0        0      0   
inmail.10010          0        0      0   0     0      0        0      1   
inmail.10011          0        0      0   0     0      0        0      0   
inmail.10012          0        0      0   0     0      0        0      0   
inmail.10013          0        0      0   0     0      0        0      0   
inmail.10014          0        0      0   0     0      0        0      0   
inmail.10015          0        0      0   0     0      0        0      0   
inmail.10016          0        0      0   0     0      0        0      0   
inmail.10017          0        0      0   0     0      0        0      1   
inmail.10018          0        0      0   0     0      0        0      0   
inmail.10019          0        0      0   0     0      0        0      0   
inmail.1002           0        0      0   0     0      0        0      1   
inmail.10022          0        0      0   0     0      0        0      0   
inmail.10024          0        0      0   0     0      0        0      0   
inmail.10025          0        0      0   0     0      0        0      0   
inmail.10026          0        1      0   0     0      0        0      0   
inmail.10027          0        0      0   0     0      0        0      0   
...                 ...      ...    ...  ..   ...    ...      ...    ...   
inmail.9970           0        0      0   0     0      0        0      0   
inmail.9971           0        0      0   0     0      0        0      0   
inmail.9972           0        0      0   0     0      0        0      0   
inmail.9974           0        0      0   0     0      1        0      0   
inmail.9975           0        0      0   0     0      0        0      0   
inmail.9976           0        0      0   0     0      0        0      0   
inmail.9977           0        0      0   0     0      0        0      0   
inmail.9978           0        0      0   0     0      0        0      0   
inmail.9979           0        0      0   0     0      0        0      0   
inmail.998            0        0      0   0     0      0        0      0   
inmail.9981           0        0      0   0     0      0        0      0   
inmail.9982           0        0      0   0     0      0        0      0   
inmail.9983           0        0      0   0     0      0        0      0   
inmail.9984           0        0      0   0     0      0        0      0   
inmail.9985           0        0      0   0     0      0        0      0   
inmail.9986           0        0      0   0     0      0        0      0   
inmail.9987           0        0      0   0     0      0        0      0   
inmail.9988           0        0      0   0     0      0        0      0   
inmail.9989           0        0      0   0     0      0        0      0   
inmail.999            0        0      0   0     0      0        0      0   
inmail.9990           0        0      0   0     0      0      

In [75]:
email_content_dict
spam_email = {}
for email in email_content_dict:
    key = email.split("/")[-1]
    spam_email[key] = email_content_dict[email]["body"]

In [76]:
spam_email

{'inmail.1': 'from sun apr smtp id apr apr generic branded apr microsoft outlook express normal ro do feel pressure perform rising anxiety thing past back old ',
 'inmail.10': 'from sun apr esmtp id apr esmtp id apr spamassassin esmtp id apr esmtp id apr apr list r mailing primary o i r find sensitivity specificity following diagnostic a particular diagnostic test multiple sclerosis conducted ms patients healthy ms patients classified healthy healthy subjects classified suffering i find number ms patients required sensitivity is simple i completely new help jochen view message sent r help mailing list archive mailing list please read posting guide reproducible ',
 'inmail.100': 'from sun apr friend esmtp id apr she wants better all apr normal microsoft outlook express produced by microsoft mimeole o this message mime html public html ',
 'inmail.1000': 'from mon apr esmtp id apr windows nt smtp id apr larry king live apr could immortality become o this message mime if mime compliant ma

In [77]:
import pickle
with open("email_content", "wb") as file:
    pickle.dump(spam_email, file)